# Yemen Accessibility to District Centers
## UTM zone 38

In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import sys, os, inspect, logging, importlib

import geopandas as gpd
import pandas as pd
import numpy as np
import osmnx as ox
import networkx as nx
from shapely.ops import split, unary_union
from shapely.geometry import box, Point

import matplotlib.pyplot as plt

In [3]:
# Get reference to GOSTNets
sys.path.append(r'../../../../GOSTnets')
import GOSTnets as gn

In [4]:
from GOSTnets.load_osm import *

In [5]:
measure_crs = 'EPSG:2089'

## Import clipped Graphs without speeds

In [6]:
G2 = nx.read_gpickle(r'yemen_regular_graph_wo_speeds3/yemen_regular_graph_wo_speeds3.pickle')

In [7]:
print(nx.info(G2))

MultiDiGraph with 142013 nodes and 355193 edges


In [8]:
gn.example_edge(G2)

('1', '110147', {'geometry': <shapely.geometry.linestring.LineString object at 0x7f0eaaa0a970>, 'id': 201859, 'one_way': False, 'osm_id': '810908760', 'Type': 'legitimate', 'infra_type': 'unclassified', 'key': 'edge_201859', 'length': 0.061233766945625, 'name': None})


## Import Origins

In [9]:
origins = gpd.read_file(r'input/hotosm_yem_populated_places_points.shp')

### split the origins between the 2 UTM zones in Yemen

In [10]:
# UTM zone 38
origins = origins.cx[42:48, 0:90]
# UTM zone 39
#origins = origins.cx[48:54, 0:90]

## Adv Snap origins to graph
The factor parameter allows you to scale up / down the unit of returned new_footway_edges if other than meters. Set to 1000 because the input length of the graph is in km.

In [11]:
%time
G_adv, pois_meter, new_footway_edges = gn.advanced_snap(G2, origins, u_tag = 'stnode', v_tag = 'endnode', node_key_col='osmid', edge_key_col='osm_id', poi_key_col='osm_id', road_col = 'infra_type', oneway_tag = 'one_way', path='output/yemen_38n', threshold=10000, knn=5, measure_crs=measure_crs, factor = 1000, verbose = True)

CPU times: user 1 µs, sys: 0 ns, total: 1 µs
Wall time: 3.34 µs
POI keys are not ints, are you sure this is okay?
Building rtree...
finished Building rtree
seconds elapsed: 23.282660722732544
updating external nodes (pois)
finished updating external nodes (pois)
seconds elapsed: 23.31283950805664
Projecting POIs to the network...2
finished pois_meter['near_idx'] and pois_meter['near_lines']
seconds elapsed: 54.37116026878357
finished pois_meter['kne_idx']
seconds elapsed: 57.131779193878174
assigning a projected point to each POI


/opt/conda/envs/geo_env/lib/python3.9/site-packages/pandas/core/dtypes/cast.py:118: ShapelyDeprecationWarning: The array interface is deprecated and will no longer work in Shapely 2.0. Convert the '.coords' to a numpy array instead.
  arr = construct_1d_object_array_from_listlike(values)


finished assigning a projected point to each POI
seconds elapsed: 60.98443102836609
Updating internal nodes...
finished Updating internal nodes
seconds elapsed: 65.63405632972717
print _new_nodes
Updating internal edges...
finished creating line_pps_dict
seconds elapsed: 68.1038818359375
creating new_lines


/home/Implementations/FY22/ACC_yemen_accessibility/../../../../GOSTnets/GOSTnets/core.py:2983: ShapelyDeprecationWarning: __len__ for multi-part geometries is deprecated and will be removed in Shapely 2.0. Check the length of the `geoms` property instead to get the  number of parts of a multi-part geometry.
  new_lines = list(split(line, pps))  # split into segments
/home/Implementations/FY22/ACC_yemen_accessibility/../../../../GOSTnets/GOSTnets/core.py:2983: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  new_lines = list(split(line, pps))  # split into segments


finished creating new_lines
seconds elapsed: 76.66605043411255
Updating update_edges


/opt/conda/envs/geo_env/lib/python3.9/site-packages/pandas/core/dtypes/cast.py:118: ShapelyDeprecationWarning: The array interface is deprecated and will no longer work in Shapely 2.0. Convert the '.coords' to a numpy array instead.
  arr = construct_1d_object_array_from_listlike(values)


debugging
finished Updating update_edges
seconds elapsed: 85.49626851081848
Updating external links...


/opt/conda/envs/geo_env/lib/python3.9/site-packages/pandas/core/dtypes/cast.py:118: ShapelyDeprecationWarning: The array interface is deprecated and will no longer work in Shapely 2.0. Convert the '.coords' to a numpy array instead.
  arr = construct_1d_object_array_from_listlike(values)


debugging
node count before: 271311
node count after: 271311
pois_meter count before: 79334
pois_meter count after: 79334
Remove edge projections greater than threshold: 22/79334 (0.03%)
finished Updating external links
seconds elapsed: 96.38383936882019
NOTE: duplication in node coordinates keys
Nodes count: 271311
Node coordinates key count: 271193
Missing 'from' nodes: 0
Missing 'to' nodes: 0
making a new graph from edges and nodes


In [12]:
originNodes = list(pois_meter['osm_id'])

In [13]:
pois_meter[:3]

osm_id population place   name source is_in  \
1  258013552.0    1527861  city  صنعاء   None  None   
2  263261532.0     458933  city    تعز   None  None   
3  263263790.0     508489  city    عدن   None  None   

                    geometry                                  near_idx  \
1  POINT (44.20588 15.35386)  [146631, 181104, 160498, 160499, 143940]   
2  POINT (44.02153 13.57522)     [76936, 191683, 11377, 76937, 110716]   
3  POINT (45.02850 12.78959)   [69025, 192744, 174749, 174748, 166590]   

                                          near_lines  kne_idx  \
1  146631    LINESTRING (414747.940 1697676.385, ...   181104   
2  76936     LINESTRING (394254.203 1500985.653, ...    76936   
3  69025     LINESTRING (503267.829 1413535.563, ...    69025   

                                              pp  
1   POINT (414810.6064762817 1697613.3285479401)  
2  POINT (394136.83818937716 1500979.8546253112)  
3  POINT (503055.60754716926 1413688.2912471865)

### Export to pickle to be used when calculating OD Matrix using graph-tool
CSVs don’t have types, that information is never preserved. CSVs only have strings. This is why we are saving as a pickle. Some of the destinations are strings, and some are ints.

In [14]:
pois_meter_export = pois_meter[['geometry','osm_id']]
pois_meter_export
pois_meter_export.to_pickle('input2/origins_38N.pickle')

### Add walking time to new footway edges

In [15]:
yemen_travel_times = {
'motorway': 40,
'motorway_link': 40,
'trunk': 40,
'trunk_link':40,
'primary': 37.5,
'primary_link': 37.5,
'secondary': 35,
'secondary_link': 35,
'tertiary':30,
'tertiary_link':30,
'residential': 20,
'unclassified': 20,
'projected_footway':3.5
}

In [16]:
# convert_network_to_time function now has 'projected_footway' as a highway class
G_adv_w_time = gn.convert_network_to_time(G_adv, 'length', road_col = 'infra_type', speed_dict = yemen_travel_times, factor=1000)

In [17]:
G_adv_w_time.nodes['20768']

{'x': 49.1780323,
 'y': 14.611084599999996,
 'geometry': <shapely.geometry.point.Point at 0x7f0e6d8954c0>,
 'infra_type': nan}

### Advanced snapping to rehab graph

In [18]:
G_adv_w_time_rehab = G_adv_w_time.copy()

### Alter times on rehab roads for rehab graph

In [19]:
count=0
for u, v, data in G_adv_w_time_rehab.edges(data=True):
    if 'Type' in data:
        if data['Type'] == 'rehab':
            print(data['Type'])
            count+=1
            # data['length'] is in meters
            # speed after rehab is 80 km per hr
            kmph = (data['length'] / 1000) / 80
            in_seconds = kmph * 60 * 60
            print(f"time before is {data['time']}")
            data['time'] = in_seconds
            print(f"time after is {data['time']}")

rehab
time before is 69.6354948802647
time after is 17.408873720066175
rehab
time before is 69.6354948802647
time after is 17.408873720066175
rehab
time before is 31.133936273084636
time after is 7.783484068271159
rehab
time before is 88.00626675737529
time after is 44.00313337868764
rehab
time before is 92.8588671647334
time after is 46.4294335823667
rehab
time before is 42.402747833508684
time after is 21.201373916754342
rehab
time before is 88.00626675737529
time after is 44.00313337868764
rehab
time before is 92.8588671647334
time after is 46.4294335823667
rehab
time before is 22.39558924684761
time after is 11.197794623423805
rehab
time before is 43.082475780236486
time after is 21.541237890118243
rehab
time before is 42.402747833508684
time after is 21.201373916754342
rehab
time before is 35.36145011215584
time after is 8.84036252803896
rehab
time before is 40.84681876571943
time after is 10.211704691429858
rehab
time before is 98.94135870188461
time after is 24.735339675471153
r

time before is 2.24669533041864
time after is 1.12334766520932
rehab
time before is 3.3929448715991697
time after is 1.6964724357995848
rehab
time before is 6.67378965413088
time after is 3.12833890037385
rehab
time before is 15.791881210808066
time after is 7.402444317566279
rehab
time before is 9.80235112239696
time after is 4.594852088623575
rehab
time before is 3.364255038793728
time after is 1.5769945494345599
rehab
time before is 8.09210269576233
time after is 4.046051347881165
rehab
time before is 2.7442765605492
time after is 1.3721382802746
rehab
time before is 8.157020083031828
time after is 3.5686962863264253
rehab
time before is 10.5620797384092
time after is 4.620909885554025
rehab
time before is 5.0314567722159085
time after is 2.2012623378444602
rehab
time before is 4.489941792833795
time after is 1.964349534364785
rehab
time before is 19.252853722273784
time after is 8.423123503494779
rehab
time before is 130.37586903085713
time after is 65.18793451542857
rehab
time bef

time after is 44.433434109299945
rehab
time before is 98.43867695417634
time after is 24.609669238544086
rehab
time before is 33.46323019292646
time after is 8.365807548231615
rehab
time before is 10.697317845488822
time after is 2.6743294613722055
rehab
time before is 5.331570632160659
time after is 1.3328926580401648
rehab
time before is 10.697317845488822
time after is 2.6743294613722055
rehab
time before is 13.998193257371348
time after is 6.124209550099965
rehab
time before is 11.928319180346946
time after is 5.218639641401789
rehab
time before is 71.68950057732732
time after is 26.883562716497746
rehab
time before is 89.57553524115714
time after is 22.393883810289285
rehab
time before is 71.68950057732732
time after is 26.883562716497746
rehab
time before is 6.634003558693321
time after is 1.6585008896733302
rehab
time before is 3.0593642427709047
time after is 0.7648410606927262
rehab
time before is 38.36382722280522
time after is 9.590956805701305
rehab
time before is 6.6340035

time before is 130.78869424396177
time after is 57.22005373173327
rehab
time before is 107.16083510358652
time after is 46.8828653578191
rehab
time before is 224.7868778256089
time after is 98.3442590487039
rehab
time before is 130.78869424396177
time after is 57.22005373173327
rehab
time before is 191.9291760399067
time after is 47.98229400997668
rehab
time before is 121.96196437277786
time after is 30.490491093194464
rehab
time before is 191.9291760399067
time after is 47.98229400997668
rehab
time before is 100.71620037165833
time after is 25.179050092914583
rehab
time before is 121.96196437277786
time after is 30.490491093194464
rehab
time before is 76.59860500572003
time after is 19.149651251430008
rehab
time before is 100.71620037165833
time after is 25.179050092914583
rehab
time before is 137.57626305182208
time after is 34.39406576295552
rehab
time before is 76.59860500572003
time after is 19.149651251430008
rehab
time before is 200.6096454044633
time after is 50.15241135111582


time after is 2.0869532173642242
rehab
time before is 1.7058258874044472
time after is 0.7462988257394456
rehab
time before is 18.947302983767102
time after is 8.289445055398106
rehab
time before is 4.770178782546798
time after is 2.0869532173642242
rehab
time before is 7.858804355505079
time after is 3.4382269055334715
rehab
time before is 18.947302983767102
time after is 8.289445055398106
rehab
time before is 0.39733883362156946
time after is 0.17383573970943664
rehab
time before is 7.858804355505079
time after is 3.4382269055334715
rehab
time before is 52.93726881991788
time after is 23.160055108714072
rehab
time before is 0.39733883362156946
time after is 0.17383573970943664
rehab
time before is 5.3597933695407125
time after is 2.344909599174062
rehab
time before is 8.376673454510373
time after is 3.6647946363482884
rehab
time before is 14.868625288854473
time after is 6.505023563873832
rehab
time before is 5.3597933695407125
time after is 2.344909599174062
rehab
time before is 11.

time after is 5.6234598228905135
rehab
time before is 0.2447340897032511
time after is 0.06118352242581278
rehab
time before is 19.17594050197172
time after is 4.79398512549293
rehab
time before is 0.034949678114271486
time after is 0.008737419528567872
rehab
time before is 0.2447340897032511
time after is 0.06118352242581278
rehab
time before is 0.13981671395185163
time after is 0.03495417848796291
rehab
time before is 0.034949678114271486
time after is 0.008737419528567872
rehab
time before is 0.2446385178800024
time after is 0.0611596294700006
rehab
time before is 0.13981671395185163
time after is 0.03495417848796291
rehab
time before is 0.10487912297508173
time after is 0.026219780743770432
rehab
time before is 0.2446385178800024
time after is 0.0611596294700006
rehab
time before is 0.03490422323543316
time after is 0.00872605580885829
rehab
time before is 0.10487912297508173
time after is 0.026219780743770432
rehab
time before is 0.13969144424733598
time after is 0.034922861061833

time before is 149.19015638222297
time after is 37.29753909555574
rehab
time before is 33.38440375729219
time after is 8.346100939323048
rehab
time before is 33.153287910310006
time after is 8.288321977577501
rehab
time before is 149.19015638222297
time after is 37.29753909555574
rehab
time before is 30.645964641763662
time after is 7.6614911604409155
rehab
time before is 33.153287910310006
time after is 8.288321977577501
rehab
time before is 30.645964641763662
time after is 7.6614911604409155


# Import Destinations

In [20]:
#destinations = gpd.read_file(r'input/HeRAMS_2018_April_snapped_renamed.shp')
#destinations = gpd.read_file(r'input/yemen_data_clusters_inland3.shp')
destinations = gpd.read_file(r'input/district_pts.shp')

### filter destinations within the correct UTM zone

In [21]:
# UTM zone 38
destinations = destinations.cx[42:48, 0:90]
# UTM zone 39
#destinations = destinations.cx[48:54, 0:90]

## Is it possible to snap to adv graph but not to POI nodes?
Yes! use the adv graph, convert it to a point_gdf, then delete all of the POI nodes, then use the point GDF to do snapping!

This will result in more precise snapping.

Also, this takes care of the following edge case:
During the adv graph creation, I had a POI lie directly on top of an existing node. Therefore the POI node replaced the existing node on the graph. Then during the snapping of destinations to the original graph, one of the destinations snapped to the node used in the original graph, but was no longer being connected to edges in the adv graph. Therefore, during the calculate_OD step this resulted in a failed path.

In [22]:
G_adv_pt_gdf = gn.node_gdf_from_graph(G_adv_w_time)
G_adv_poi_pts = G_adv_pt_gdf.loc[G_adv_pt_gdf['infra_type'] != 'poi']

In [23]:
snapped_destinations_df = gn.pandana_snap_c(G_adv_poi_pts, destinations, source_crs='epsg:4326', target_crs=measure_crs)

In [24]:
snapped_destinations_df[:3]

id  name  pop                   geometry      NN     NN_dist
0   1  None  NaN  POINT (43.25045 13.81234)   81206  238.315398
1   2  None  NaN  POINT (43.46569 13.94190)   27399  266.603817
2   3  None  NaN  POINT (43.67727 14.03854)  126639  178.270568

### Export to pickle to be used when calculating OD Matrix using graph-tool

CSVs don’t have types, that information is never preserved. CSVs only have strings. This is why we are saving as a pickle. Some of the destinations are strings, and some are ints.

In [25]:
snapped_destinations_df[['NN']].to_pickle('input2/destinations_districts_38N.pickle')

In [26]:
destinationNodes = list(snapped_destinations_df['NN'].unique())

In [27]:
destinationNodes

['81206',
 '27399',
 '126639',
 'new_obj_889',
 'new_obj_1043',
 'new_obj_880',
 '105921',
 'new_obj_902',
 '160984',
 9990035389,
 9990039456,
 '46562',
 'new_obj_3123',
 '142199',
 '57319',
 '148766',
 '145119',
 9990049311,
 '10957',
 '159174',
 '497',
 '128883',
 '129309',
 '151913',
 '124348',
 9990037111,
 '17845',
 9990038999,
 '148641',
 9990008831,
 9990008747,
 '97789',
 '24665',
 '86997',
 '78291',
 9990030295,
 '16043',
 9990040446,
 '7980',
 '46364',
 '65612',
 '1786',
 9990000009,
 '57724',
 '111266',
 '58859',
 9990002665,
 9990016667,
 9990016898,
 9990020104,
 '127237',
 9990034807,
 9990037308,
 9990025268,
 9990016144,
 '71985',
 9990048699,
 9990046148,
 9990013591,
 9990046726,
 9990007569,
 9990004686,
 '59122',
 9990004711,
 9990012458,
 9990012414,
 9990004883,
 9990045345,
 9990007290,
 9990048144,
 '164668',
 9990046077,
 9990012519,
 '56447',
 9990007152,
 9990014075,
 9990045656,
 9990015791,
 9990015483,
 9990022313,
 9990028514,
 '75143',
 9990022559,
 999

## Export Graphs to be run in Calculate OD using graph-tool

In [28]:
G_adv_w_time_export = G_adv_w_time.copy()

In [29]:
for n1, n2, data in G_adv_w_time_export.edges(data=True):
    #print(data)
    #del data['infra_type']
    #del data['Type']
    #del data['mode']
    del data['key']
    del data['name']
    del data['id']

In [30]:
for node, data in G_adv_w_time_export.nodes(data=True):
    #print(data)
    del data['infra_type']

In [31]:
G_adv_edges2 = gn.edge_gdf_from_graph(G_adv_w_time_export)
G_adv_edges2[:3]

stnode endnode     osm_id       time   mode    infra_type  one_way  \
0      1  110147  810908760  11.022078  drive  unclassified    False   
1      1  144649  810908766  27.985998  drive  unclassified    False   
2      1   21643  810908760  11.121738  drive  unclassified    False   

         Type      length                                           geometry  
0  legitimate   61.233767  LINESTRING (44.18929 15.45383, 44.18931 15.45438)  
1  legitimate  155.477768  LINESTRING (44.18929 15.45383, 44.18784 15.45386)  
2  legitimate   61.787434  LINESTRING (44.18927 15.45327, 44.18929 15.45383)

In [32]:
G_adv_nodes2 = gn.node_gdf_from_graph(G_adv_w_time_export)
G_adv_nodes2[:3]

node_ID          x          y                   geometry
0       1  44.189288  15.453828  POINT (44.18929 15.45383)
1  110147  44.189306  15.454381  POINT (44.18931 15.45438)
2  144649  44.187839  15.453862  POINT (44.18784 15.45386)

In [33]:
#gn.save(G_adv_w_time_export, 'G_adv_w_time', 'input2', pickle=True, edges=True, nodes=True)

In [34]:
G_adv_w_time_rehab_export = G_adv_w_time_rehab.copy()

In [35]:
for n1, n2, data in G_adv_w_time_rehab_export.edges(data=True):
    #print(data)
    del data['infra_type']
    del data['Type']
    del data['mode']
    del data['key']
    del data['name']
    del data['id']

In [36]:
for node, data in G_adv_w_time_rehab_export.nodes(data=True):
    #print(data)
    del data['infra_type']

In [37]:
G_adv_edges3 = gn.edge_gdf_from_graph(G_adv_w_time_rehab_export)
G_adv_edges3

stnode     endnode                   osm_id        time  \
0                  1      110147                810908760   11.022078   
1                  1      144649                810908766   27.985998   
2                  1       21643                810908760   11.121738   
3             110147       96034                810908760   51.482333   
4             110147       46500                810908765   28.098010   
...              ...         ...                      ...         ...   
529092  8941401868.0  9990049963  9990049963_8941401868.0   54.567299   
529093  8996326622.0      128985      128985_8996326622.0  116.480543   
529094  8996697205.0       31124       31124_8996697205.0  140.163602   
529095  8999185829.0       31124       31124_8999185829.0  129.396835   
529096  8999185830.0      128985      128985_8999185830.0   53.226851   

        one_way      length                                           geometry  
0         False   61.233767  LINESTRING (44.18929 15.45383, 44.18931 15.45438)  
1         False  155.477768  LINESTRING (44.18929 15.45383, 44.18784 15.45386)  
2         False   61.787434  LINESTRING (44.18927 15.45327, 44.18929 15.45383)  
3         False  286.012964  LINESTRING (44.18931 15.45438, 44.18933 15.454...  
4         False  156.100053  LINESTRING (44.18785 15.45441, 44.18931 15.45438)  
...         ...         ...                                                ...  
529092     True   53.051541  LINESTRING (44.14249 14.58104, 44.14201 14.58115)  
529093     True  113.244972  LINESTRING (44.88386 13.01905, 44.88481 13.01949)  
529094     True  136.270169  LINESTRING (44.88357 13.01881, 44.88479 13.01850)  
529095     True  125.802478  LINESTRING (44.88363 13.01848, 44.88479 13.01850)  
529096     True   51.748327  LINESTRING (44.88443 13.01920, 44.88481 13.01949)  

[529097 rows x 7 columns]

In [38]:
#gn.save(G_adv_w_time_rehab_export, 'G_adv_w_time_rehab', 'input2', pickle=True, edges=True, nodes=True)

## Calculate OD matrix for regular graph

In [103]:
%%time
#OD_matrix = gn.calculate_OD(G_adv_w_time, originNodes, destinationNodes, fail_value=-1, weight='time', one_way_roads_exist = True)

CPU times: user 0 ns, sys: 9 µs, total: 9 µs
Wall time: 26.2 µs


In [104]:
# load OD matrix from CSV
OD_matrix = pd.read_pickle(r'output2/OD_matrix_district_38N.pickle')

In [105]:
OD_matrix

9990019074         58859    9990036997    9990046726  \
1.219232e+09  61506.985968  31222.783173  29075.044199  15627.616932   
1.219232e+09  60635.801323  30351.598528  29028.688434  14756.432287   
1.219232e+09  60390.494761  30106.291965  29284.028380  14511.125725   
1.219232e+09  60709.856131  30425.653336  28277.914362  14830.487095   
1.219232e+09  63061.392721  32777.189925  31954.926340  17182.023685   
...                    ...           ...           ...           ...   
6.936545e+09  54317.002312   7746.081703  47299.052583  31494.977955   
6.936545e+09  54362.640089   7791.719479  47344.690359  31540.615731   
5.699797e+09  44353.482922  19218.321895  36678.619653  20581.631448   
6.936545e+09  54372.251435   7801.330826  46612.560610  31550.227078   
6.936545e+09  53860.473989   7289.553379  46316.699431  31038.449631   

                     59122         24665    9990020104    9990049796  \
1.219232e+09   8751.093198  14861.558667  29812.551899  49005.200277   
1.219232e+09   8704.737434  13990.374022  28941.367254  48134.015632   
1.219232e+09   8960.077379  13745.067459  28696.060691  47888.709069   
1.219232e+09   7953.963361  14064.428830  29015.422062  48208.070439   
1.219232e+09  11630.975339  16415.965419  31366.958651  50559.607029   
...                    ...           ...           ...           ...   
6.936545e+09  35161.683968  33891.171330   8509.988634  22870.960347   
6.936545e+09  35207.321744  33936.809106   8555.626410  22916.598123   
5.699797e+09  22154.372953  20883.860315  14646.639183  26406.865061   
6.936545e+09  34475.191995  33204.679357   7823.496661  22926.209470   
6.936545e+09  34179.330817  32908.818178   7527.635482  22414.432023   

                       497        122404  ...         97789  new_obj_3123  \
1.219232e+09  15069.885939  51956.251737  ...   8736.974299  14592.847015   
1.219232e+09  15023.530175  51085.067092  ...   8690.618535  13721.662370   
1.219232e+09  15278.870120  50839.760529  ...   8945.958480  13476.355807   
1.219232e+09  14272.756102  51159.121900  ...   7939.844462  13795.717178   
1.219232e+09  17949.768080  53510.658489  ...  11616.856440  16147.253767   
...                    ...           ...  ...           ...           ...   
6.936545e+09  33293.894323  20050.247636  ...  35147.565069  23515.110824   
6.936545e+09  33339.532099  20095.885412  ...  35193.202845  23560.748600   
5.699797e+09  22673.461393  28268.920325  ...  22140.254054  19086.899366   
6.936545e+09  32607.402350  20105.496759  ...  34461.073096  22828.618851   
6.936545e+09  32311.541171  19593.719312  ...  34165.211917  22532.757672   

                     46364        140374         63338         26865  \
1.219232e+09  22116.088379  41712.781186  52746.139096  42982.298540   
1.219232e+09  21244.903734  41666.425422  51874.954451  42111.113895   
1.219232e+09  20999.597172  41921.765367  51629.647889  41865.807332   
1.219232e+09  21318.958542  40915.651349  51949.009259  42185.168703   
1.219232e+09  23670.495132  44592.663327  54300.545849  44536.705292   
...                    ...           ...           ...           ...   
6.936545e+09  17171.592496  53361.996628  20840.134995  11076.294439   
6.936545e+09  17217.230272  53407.634404  20885.772771  11121.932215   
5.699797e+09  14023.868476  42448.650121  29058.807684  22271.231906   
6.936545e+09  16485.100523  53417.245751  20895.384118  11131.543562   
6.936545e+09  16189.239344  52905.468304  20383.606671  10619.766115   

                9990014970    9990015483    9990012414    9990033919  
1.219232e+09  34991.657318  20804.008633  14601.491846  24130.277659  
1.219232e+09  34120.472673  20757.652869  14555.136081  24083.921894  
1.219232e+09  33875.166110  21012.992814  14810.476027  24339.261839  
1.219232e+09  34194.527480  20006.878796  13804.362009  23333.147822  
1.219232e+09  36546.064070  23683.890774  17481.373987  27010.159800  
...                    ...           ...           ...           ...  

In [106]:
OD_matrix.min(axis=1)

1.219232e+09    8021.665379
1.219232e+09    7150.480734
1.219232e+09    6905.174172
1.219232e+09    7224.535542
1.219232e+09    9576.072132
                   ...     
6.936545e+09    4191.786077
6.936545e+09    4237.423854
5.699797e+09    1401.688051
6.936545e+09    4247.035200
6.936545e+09    3735.257754
Length: 79334, dtype: float64

In [107]:
colName = "travel_time_to_closest_facility"
results = pd.DataFrame({'osm_id':OD_matrix.min(axis=1).index, colName:OD_matrix.min(axis=1).values})
results

osm_id  travel_time_to_closest_facility
0      1.219232e+09                      8021.665379
1      1.219232e+09                      7150.480734
2      1.219232e+09                      6905.174172
3      1.219232e+09                      7224.535542
4      1.219232e+09                      9576.072132
...             ...                              ...
79329  6.936545e+09                      4191.786077
79330  6.936545e+09                      4237.423854
79331  5.699797e+09                      1401.688051
79332  6.936545e+09                      4247.035200
79333  6.936545e+09                      3735.257754

[79334 rows x 2 columns]

In [108]:
# test
results[results['travel_time_to_closest_facility']==-1]

Empty DataFrame
Columns: [osm_id, travel_time_to_closest_facility]
Index: []

In [109]:
output2 = pd.merge(pois_meter, results, on="osm_id")

In [110]:
output2[["travel_time_to_closest_facility"]] = output2[["travel_time_to_closest_facility"]].apply(pd.to_numeric)

In [111]:
output2 = output2.drop(columns=['near_idx','near_lines','pp'], axis=1)

In [112]:
output2['travel_time_to_closest_facility'].mean()

3792.7337877880937

In [113]:
output2

osm_id population    place          name source is_in  \
0      2.580136e+08    1527861     city         صنعاء   None  None   
1      2.632615e+08     458933     city           تعز   None  None   
2      2.632638e+08     508489     city           عدن   None  None   
3      2.682568e+08     208844     city            إب   None  None   
4      2.965122e+08     144273     city          ذمار   None  None   
...             ...        ...      ...           ...    ...   ...   
79329  8.941402e+09        261  village  وادي الامحال   None  None   
79330  8.996327e+09       None     town          None   None  None   
79331  8.996697e+09       None     town          None   None  None   
79332  8.999186e+09       None     town          None   None  None   
79333  8.999186e+09       None     town          None   None  None   

                        geometry  kne_idx  travel_time_to_closest_facility  
0      POINT (44.20588 15.35386)   181104                       180.962647  
1      POINT (44.02153 13.57522)    76936                       294.926379  
2      POINT (45.02850 12.78959)    69025                       404.496136  
3      POINT (44.17794 13.97016)    81160                       361.693173  
4      POINT (44.40006 14.54300)     9472                       151.022287  
...                          ...      ...                              ...  
79329  POINT (44.14249 14.58104)   171125                       410.263805  
79330  POINT (44.88386 13.01905)    84302                       836.801385  
79331  POINT (44.88357 13.01881)    87578                       907.118601  
79332  POINT (44.88363 13.01848)    87578                       896.351834  
79333  POINT (44.88443 13.01920)    84302                       773.547692  

[79334 rows x 9 columns]

In [114]:
reg_accessibilty_gpd = gpd.GeoDataFrame(output2, crs = "epsg:4326", geometry = 'geometry')
#reg_accessibilty_gpd.to_file('yemen_accessibility_district_centers_wo_walking_time2.shp')
#reg_accessibilty_gpd.to_file('yemen_38n_accessibility_district_centers_w_walking_time3.shp')
reg_accessibilty_gpd.to_file('output2/yemen_38n_accessibility_district_centers_w_walking_time_6.shp')

<ipython-input-114-88e2de7f9c5e>:4: UserWarning: Column names longer than 10 characters will be truncated when saved to ESRI Shapefile.
  reg_accessibilty_gpd.to_file('output2/yemen_38n_accessibility_district_centers_w_walking_time_6.shp')


## Calculate OD matrix for graph with rehabilitated roads

In [115]:
#OD_matrix2 = gn.calculate_OD(G_adv_w_time_rehab, originNodes, destinationNodes, fail_value=-1, weight='time', one_way_roads_exist = True)

In [116]:
# load OD matrix from CSV
OD_matrix2 = pd.read_pickle(r'output2/OD_matrix_district_38N_rehab.pickle')

In [117]:
OD_matrix2

9990019074        148766    9990036997    9990046726  \
1.219232e+09  61506.985968  15104.403183  29075.044199  15627.616932   
1.219232e+09  60635.801323  14233.218538  29028.688434  14756.432287   
1.219232e+09  60390.494761  13987.911975  29284.028380  14511.125725   
1.219232e+09  60709.856131  14307.273346  28277.914362  14830.487095   
1.219232e+09  63061.392721  16658.809935  31954.926340  17182.023685   
...                    ...           ...           ...           ...   
6.936545e+09  54317.002312  29256.590107  47299.052583  31494.977955   
6.936545e+09  54362.640089  29302.227883  47344.690359  31540.615731   
5.699797e+09  44353.482922  19835.066458  36678.619653  20581.631448   
6.936545e+09  54372.251435  28570.098134  46612.560610  31550.227078   
6.936545e+09  53860.473989  28274.236956  46316.699431  31038.449631   

              new_obj_1916    9990020104  new_obj_2018    9990049796  \
1.219232e+09  28096.689554  29812.551899  35191.886807  48738.739076   
1.219232e+09  27225.504909  28941.367254  34320.702162  47867.554430   
1.219232e+09  26980.198346  28696.060691  34075.395599  47622.247868   
1.219232e+09  27299.559717  29015.422062  34394.756970  47941.609238   
1.219232e+09  29651.096306  31366.958651  36746.293559  50293.145828   
...                    ...           ...           ...           ...   
6.936545e+09  18160.812991   8183.849275  10271.189272  22621.419105   
6.936545e+09  18206.450767   8229.487051  10316.827048  22667.056881   
5.699797e+09   7619.790359  14646.639183   8077.623332  26140.403860   
6.936545e+09  18216.062114   7497.357302  10326.438395  22676.668227   
6.936545e+09  17704.284667   7201.496123   9814.660948  22164.890781   

                9990047761    9990041105  ...    9990012399         60698  \
1.219232e+09  23889.526601  28637.853219  ...  15704.909985  18275.625929   
1.219232e+09  23843.170836  27766.668573  ...  15658.554221  18229.270165   
1.219232e+09  24098.510782  27521.362011  ...  15913.894166  18484.610110   
1.219232e+09  23092.396764  27840.723381  ...  14907.780148  17478.496092   
1.219232e+09  26769.408742  30192.259971  ...  18584.792126  21155.508070   
...                    ...           ...  ...           ...           ...   
6.936545e+09  35538.742043  19947.560309  ...  31395.483480  31717.438705   
6.936545e+09  35584.379819  19993.198085  ...  31441.121256  31763.076481   
5.699797e+09  24625.395536   3140.585137  ...  20482.136973  20804.092198   
6.936545e+09  35593.991166  20002.809432  ...  31450.732603  31772.687828   
6.936545e+09  35082.213719  19491.031985  ...  30938.955156  31260.910381   

                    104006       9999046         70907         20004  \
1.219232e+09  28450.724349  42746.021832  34629.025570  51262.035257   
1.219232e+09  27579.539704  41874.837187  34582.669805  50390.850612   
1.219232e+09  27334.233141  41629.530624  34838.009751  50145.544049   
1.219232e+09  27653.594512  41948.891995  33831.895733  50464.905420   
1.219232e+09  30005.131101  44300.428584  37508.907711  52816.442010   
...                    ...           ...           ...           ...   
6.936545e+09  18583.014972  32232.642028  46278.241012  19751.241179   
6.936545e+09  18628.652748  32278.279804  46323.878788  19796.878955   
5.699797e+09   7980.446281  22269.122637  35364.894505  28518.499700   
6.936545e+09  18638.264095  32287.891151  46333.490135  19806.490302   
6.936545e+09  18126.486648  31776.113704  45821.712688  19294.712855   

                9990014970    9990015483    9990012414    9990033919  
1.219232e+09  34991.657318  20804.008633  14601.491846  24130.277659  
1.219232e+09  34120.472673  20757.652869  14555.136081  24083.921894  
1.219232e+09  33875.166110  21012.992814  14810.476027  24339.261839  
1.219232e+09  34194.527480  20006.878796  13804.362009  23333.147822  
1.219232e+09  36546.064070  23683.890774  17481.373987  27010.159800  
...                    ...           ...           ...           ...  

In [118]:
%%time
# closest_facility_per_origin2 = OD_matrix2.min(axis=1)
# results2 = pd.DataFrame([originNodes, closest_facility_per_origin2]).transpose()
# colName = "travel_time_to_closest_facility"
# results2.columns = ['osm_id', colName]

colName = "travel_time_to_closest_facility"
results2 = pd.DataFrame({'osm_id':OD_matrix2.min(axis=1).index, colName:OD_matrix2.min(axis=1).values})
results2

CPU times: user 85.9 ms, sys: 0 ns, total: 85.9 ms
Wall time: 85 ms


osm_id  travel_time_to_closest_facility
0      1.219232e+09                      8021.665379
1      1.219232e+09                      7150.480734
2      1.219232e+09                      6905.174172
3      1.219232e+09                      7224.535542
4      1.219232e+09                      9576.072132
...             ...                              ...
79329  6.936545e+09                      4174.934696
79330  6.936545e+09                      4220.572472
79331  5.699797e+09                      1401.688051
79332  6.936545e+09                      4230.183819
79333  6.936545e+09                      3718.406372

[79334 rows x 2 columns]

In [119]:
output3 = pd.merge(pois_meter, results2, on="osm_id")
output3[["travel_time_to_closest_facility"]] = output3[["travel_time_to_closest_facility"]].apply(pd.to_numeric)

In [120]:
output3['travel_time_to_closest_facility'].mean()

3724.5266475405547

In [121]:
output3 = output3.drop(columns=['near_idx','near_lines','pp'], axis=1)

In [122]:
accessibilty_gpd = gpd.GeoDataFrame(output3, crs = "epsg:4326", geometry = 'geometry')
#accessibilty_gpd.to_file('yemen_accessibility_district_centers_rehabbed_wo_walking_time2.shp')
#accessibilty_gpd.to_file('yemen_38n_accessibility_district_centers_rehabbed_w_walking_time3.shp')
accessibilty_gpd.to_file('output2/yemen_38n_accessibility_district_centers_w_walking_time_rehab_6.shp')

<ipython-input-122-2f1d1d26473b>:4: UserWarning: Column names longer than 10 characters will be truncated when saved to ESRI Shapefile.
  accessibilty_gpd.to_file('output2/yemen_38n_accessibility_district_centers_w_walking_time_rehab_6.shp')


## Calculate average travel time per Rehabilitated road

In [123]:
origins_to_closest_facility_gpd = gpd.GeoDataFrame(output2, crs = "epsg:4326", geometry = 'geometry')

In [124]:
origins_to_closest_facility_gpd

osm_id population    place          name source is_in  \
0      2.580136e+08    1527861     city         صنعاء   None  None   
1      2.632615e+08     458933     city           تعز   None  None   
2      2.632638e+08     508489     city           عدن   None  None   
3      2.682568e+08     208844     city            إب   None  None   
4      2.965122e+08     144273     city          ذمار   None  None   
...             ...        ...      ...           ...    ...   ...   
79329  8.941402e+09        261  village  وادي الامحال   None  None   
79330  8.996327e+09       None     town          None   None  None   
79331  8.996697e+09       None     town          None   None  None   
79332  8.999186e+09       None     town          None   None  None   
79333  8.999186e+09       None     town          None   None  None   

                        geometry  kne_idx  travel_time_to_closest_facility  
0      POINT (44.20588 15.35386)   181104                       180.962647  
1      POINT (44.02153 13.57522)    76936                       294.926379  
2      POINT (45.02850 12.78959)    69025                       404.496136  
3      POINT (44.17794 13.97016)    81160                       361.693173  
4      POINT (44.40006 14.54300)     9472                       151.022287  
...                          ...      ...                              ...  
79329  POINT (44.14249 14.58104)   171125                       410.263805  
79330  POINT (44.88386 13.01905)    84302                       836.801385  
79331  POINT (44.88357 13.01881)    87578                       907.118601  
79332  POINT (44.88363 13.01848)    87578                       896.351834  
79333  POINT (44.88443 13.01920)    84302                       773.547692  

[79334 rows x 9 columns]

In [125]:
origins_to_closest_facility_gpd_prj = origins_to_closest_facility_gpd.to_crs(measure_crs)

### Read fille of 5k buffers around roads
QGIS steps: select all rehab roads, save a 38N projection, buffer, dissolve, then multi-part to single-part

In [126]:
rehab_rds_yemen_38n_5k_buffer = gpd.read_file(r'rehab_rds_only_G_largest_cleaned_yemen4_single_edge2_38n_5k_buffer5.shp')

In [127]:
rehab_rds_yemen_38n_5k_buffer

stnode endnode     id  one_way     osm_id   Type infra_type         key  \
0     170  147350  91987        0  436184635  rehab      trunk  edge_91987   
1     170  147350  91987        0  436184635  rehab      trunk  edge_91987   
2     170  147350  91987        0  436184635  rehab      trunk  edge_91987   
3     170  147350  91987        0  436184635  rehab      trunk  edge_91987   
4     170  147350  91987        0  436184635  rehab      trunk  edge_91987   
5     170  147350  91987        0  436184635  rehab      trunk  edge_91987   
6     170  147350  91987        0  436184635  rehab      trunk  edge_91987   
7     170  147350  91987        0  436184635  rehab      trunk  edge_91987   
8     170  147350  91987        0  436184635  rehab      trunk  edge_91987   
9     170  147350  91987        0  436184635  rehab      trunk  edge_91987   
10    170  147350  91987        0  436184635  rehab      trunk  edge_91987   
11    170  147350  91987        0  436184635  rehab      trunk  edge_91987   
12    170  147350  91987        0  436184635  rehab      trunk  edge_91987   
13    170  147350  91987        0  436184635  rehab      trunk  edge_91987   
14    170  147350  91987        0  436184635  rehab      trunk  edge_91987   
15    170  147350  91987        0  436184635  rehab      trunk  edge_91987   
16    170  147350  91987        0  436184635  rehab      trunk  edge_91987   
17    170  147350  91987        0  436184635  rehab      trunk  edge_91987   
18    170  147350  91987        0  436184635  rehab      trunk  edge_91987   
19    170  147350  91987        0  436184635  rehab      trunk  edge_91987   
20    170  147350  91987        0  436184635  rehab      trunk  edge_91987   
21    170  147350  91987        0  436184635  rehab      trunk  edge_91987   
22    170  147350  91987        0  436184635  rehab      trunk  edge_91987   

      length              name  \
0   0.977847  al_abr_to_seiyun   
1   0.977847  al_abr_to_seiyun   
2   0.977847  al_abr_to_seiyun   
3   0.977847  al_abr_to_seiyun   
4   0.977847  al_abr_to_seiyun   
5   0.977847  al_abr_to_seiyun   
6   0.977847  al_abr_to_seiyun   
7   0.977847  al_abr_to_seiyun   
8   0.977847  al_abr_to_seiyun   
9   0.977847  al_abr_to_seiyun   
10  0.977847  al_abr_to_seiyun   
11  0.977847  al_abr_to_seiyun   
12  0.977847  al_abr_to_seiyun   
13  0.977847  al_abr_to_seiyun   
14  0.977847  al_abr_to_seiyun   
15  0.977847  al_abr_to_seiyun   
16  0.977847  al_abr_to_seiyun   
17  0.977847  al_abr_to_seiyun   
18  0.977847  al_abr_to_seiyun   
19  0.977847  al_abr_to_seiyun   
20  0.977847  al_abr_to_seiyun   
21  0.977847  al_abr_to_seiyun   
22  0.977847  al_abr_to_seiyun   

                                             geometry  
0   POLYGON ((423850.447 1450694.145, 423836.637 1...  
1   POLYGON ((372427.033 1512304.025, 372581.704 1...  
2   POLYGON ((402505.912 1607646.041, 402493.142 1...  
3   POLYGON ((417612.078 1548291.364, 418798.561 1...  
4   POLYGON ((416288.856 1561210.961, 415879.644 1...  
5   POLYGON ((502841.446 1575046.924, 501576.664 1...  
6   POLYGON ((468920.058 1584746.367, 468703.966 1...  
7   POLYGON ((542731.058 1447148.254, 542648.482 1...  
8   POLYGON ((485036.171 1506022.583, 485086.685 1...  
9   POLYGON ((471249.443 1501611.368, 469790.402 1...  
10  POLYGON ((472515.969 1542843.521, 472612.627 1...  
11  POLYGON ((555564.336 1560240.666, 555948.184 1...  
12  POLYGON ((529302.623 1617648.101, 529307.215 1...  
13  POLYGON ((529120.156 1670767.392, 529340.762 1...  
14  POLYGON ((835466.150 1738882.284, 835029.277 1...  
15  POLYGON ((443321.134 1630278.485, 443381.265 1...  
16  POLYGON ((514968.926 1660699.785, 514950.002 1...  
17  POLYGON ((937190.004 1630380.011, 936943.220 1...  
18  POLYGON ((325934.798 1607559.522, 325900.967 1...  
19  POLYGON ((288092.058 1665795.417, 288314.607 1...  
20  POLYGON ((372684.113 1660200.166, 372329.775 1...  
21  POLYGON ((338664.273 1723803.406, 337689.817 1...  
22  POLYGON ((296229.837 

In [128]:
rehab_rds_yemen_38n_5k_buffer.crs

<Derived Projected CRS: EPSG:32638>
Name: WGS 84 / UTM zone 38N
Axis Info [cartesian]:
- E[east]: Easting (metre)
- N[north]: Northing (metre)
Area of Use:
- name: Between 42°E and 48°E, northern hemisphere between equator and 84°N, onshore and offshore. Armenia. Azerbaijan. Djibouti. Eritrea. Ethiopia. Georgia. Islamic Republic of Iran. Iraq. kazakhstan. Kuwait. Russian Federation. Saudi Arabia. Somalia. Turkey. Yemen.
- bounds: (42.0, 0.0, 48.0, 84.0)
Coordinate Operation:
- name: UTM zone 38N
- method: Transverse Mercator
Datum: World Geodetic System 1984 ensemble
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

In [129]:
rehab_rds_yemen_38n_5k_buffer.iloc[[0]]

stnode endnode     id  one_way     osm_id   Type infra_type         key  \
0    170  147350  91987        0  436184635  rehab      trunk  edge_91987   

     length              name  \
0  0.977847  al_abr_to_seiyun   

                                            geometry  
0  POLYGON ((423850.447 1450694.145, 423836.637 1...

In [130]:
points_within = gpd.sjoin(origins_to_closest_facility_gpd_prj, rehab_rds_yemen_38n_5k_buffer, op='within')

/opt/conda/envs/geo_env/lib/python3.9/site-packages/IPython/core/interactiveshell.py:3377: FutureWarning: The `op` parameter is deprecated and will be removed in a future release. Please use the `predicate` parameter instead.
  if (await self.run_code(code, result,  async_=asy)):
<ipython-input-130-eea28ffc0127>:1: UserWarning: CRS mismatch between the CRS of left geometries and the CRS of right geometries.
Use `to_crs()` to reproject one of the input geometries to match the CRS of the other.

Left CRS: EPSG:2089
Right CRS: EPSG:32638

  points_within = gpd.sjoin(origins_to_closest_facility_gpd_prj, rehab_rds_yemen_38n_5k_buffer, op='within')


In [131]:
points_within

osm_id_left population              place           name_left source  \
1      2.632615e+08     458933               city                 تعز   None   
32     1.216827e+09        170             hamlet               النجد   None   
3214   1.219306e+09        108             hamlet          قرية الدار   None   
3215   1.219306e+09         81             hamlet             الكريفة   None   
3216   1.219306e+09        111             hamlet         شعب العكاري   None   
...             ...        ...                ...                 ...    ...   
61839  6.936989e+09       None             hamlet             المشرقي   None   
62036  6.936989e+09         11             hamlet               الكتف   None   
62101  6.936989e+09       None             hamlet         ذراع العطيف   None   
62296  6.936989e+09       None             hamlet              الريام   None   
62803  7.283154e+09       None  isolated_dwelling  مفرق طريق جبل مراد   None   

      is_in                        geometry  kne_idx  \
1      None  POINT (394138.111 1500961.213)    76936   
32     None  POINT (427254.748 1452614.479)    17583   
3214   None  POINT (386005.958 1496432.056)   143245   
3215   None  POINT (381276.675 1497180.431)    72140   
3216   None  POINT (382131.260 1500861.181)    95237   
...     ...                             ...      ...   
61839  None  POINT (526893.454 1661136.746)    17134   
62036  None  POINT (524498.331 1669565.424)   179783   
62101  None  POINT (521608.007 1660419.052)   101459   
62296  None  POINT (522783.917 1667152.607)    57586   
62803  None  POINT (531689.382 1666396.595)   173709   

       travel_time_to_closest_facility  index_right stnode endnode     id  \
1                           294.926379            0    170  147350  91987   
32                          557.396882            0    170  147350  91987   
3214                       1248.057520            0    170  147350  91987   
3215                       4272.792044            0    170  147350  91987   
3216                       1725.848893            0    170  147350  91987   
...                                ...          ...    ...     ...    ...   
61839                      4949.866870           13    170  147350  91987   
62036                      4074.923675           13    170  147350  91987   
62101                      3547.906044           13    170  147350  91987   
62296                      5874.877934           13    170  147350  91987   
62803                       891.537163           13    170  147350  91987   

       one_way osm_id_right   Type infra_type         key    length  \
1            0    436184635  rehab      trunk  edge_91987  0.977847   
32           0    436184635  rehab      trunk  edge_91987  0.977847   
3214         0    436184635  rehab      trunk  edge_91987  0.977847   
3215         0    436184635  rehab      trunk  edge_91987  0.977847   
3216         0    436184635  rehab      trunk  edge_91987  0.977847   
...        ...          ...    ...        ...         ...       ...   
61839        0    436184635  rehab      trunk  edge_91987  0.977847   
62036        0    436184635  rehab      trunk  edge_91987  0.977847   
62101        0    436184635  rehab      trunk  edge_91987  0.977847   
62296        0    436184635  rehab      trunk  edge_91987  0.977847   
62803        0    436184635  rehab      trunk  edge_91987  0.977847   

             name_right  
1      al_abr_to_seiyun  
32     al_abr_to_seiyun  
3214   al_abr_to_seiyun  
3215   al_abr_to_seiyun  
3216   al_abr_to_seiyun  
...                 ...  
61839  al_abr_to_seiyun  
62036  al_abr_to_seiyun  
62101  al_abr_to_seiyun  
62296  al_abr_to_seiyun  
62803  al_abr_to_seiyun  

[10090 rows x 20 columns]

In [132]:
list(points_within['osm_id_left'])

[263261532.0,
 1216827057.0,
 1219305839.0,
 1219305844.0,
 1219305850.0,
 1219305853.0,
 1219305862.0,
 1219305888.0,
 1219305896.0,
 1219305906.0,
 1219305927.0,
 1219305933.0,
 1219305958.0,
 1219305995.0,
 1219305998.0,
 1219306016.0,
 1219306017.0,
 1219306019.0,
 1219306034.0,
 1219306038.0,
 1219306120.0,
 1219306141.0,
 1219306149.0,
 1219306153.0,
 1219306164.0,
 1219306168.0,
 1219306172.0,
 1219306191.0,
 1219306858.0,
 1219306868.0,
 1219306871.0,
 1219306909.0,
 1219306975.0,
 1219307014.0,
 1219307018.0,
 1219307037.0,
 1219307062.0,
 1219307076.0,
 1219307081.0,
 1219307101.0,
 1219307134.0,
 1219307206.0,
 1219307225.0,
 1219307255.0,
 1219307285.0,
 1219307336.0,
 1219307450.0,
 1219307578.0,
 1219398896.0,
 1219398925.0,
 1219398962.0,
 1219398994.0,
 1219399038.0,
 1219399234.0,
 1219399431.0,
 1219399445.0,
 1219399470.0,
 1219399619.0,
 1219399632.0,
 1219399693.0,
 1219399801.0,
 1219399972.0,
 1219400060.0,
 1219400098.0,
 1219401981.0,
 1219401997.0,
 1219403426

In [133]:
OD_matrix2

9990019074        148766    9990036997    9990046726  \
1.219232e+09  61506.985968  15104.403183  29075.044199  15627.616932   
1.219232e+09  60635.801323  14233.218538  29028.688434  14756.432287   
1.219232e+09  60390.494761  13987.911975  29284.028380  14511.125725   
1.219232e+09  60709.856131  14307.273346  28277.914362  14830.487095   
1.219232e+09  63061.392721  16658.809935  31954.926340  17182.023685   
...                    ...           ...           ...           ...   
6.936545e+09  54317.002312  29256.590107  47299.052583  31494.977955   
6.936545e+09  54362.640089  29302.227883  47344.690359  31540.615731   
5.699797e+09  44353.482922  19835.066458  36678.619653  20581.631448   
6.936545e+09  54372.251435  28570.098134  46612.560610  31550.227078   
6.936545e+09  53860.473989  28274.236956  46316.699431  31038.449631   

              new_obj_1916    9990020104  new_obj_2018    9990049796  \
1.219232e+09  28096.689554  29812.551899  35191.886807  48738.739076   
1.219232e+09  27225.504909  28941.367254  34320.702162  47867.554430   
1.219232e+09  26980.198346  28696.060691  34075.395599  47622.247868   
1.219232e+09  27299.559717  29015.422062  34394.756970  47941.609238   
1.219232e+09  29651.096306  31366.958651  36746.293559  50293.145828   
...                    ...           ...           ...           ...   
6.936545e+09  18160.812991   8183.849275  10271.189272  22621.419105   
6.936545e+09  18206.450767   8229.487051  10316.827048  22667.056881   
5.699797e+09   7619.790359  14646.639183   8077.623332  26140.403860   
6.936545e+09  18216.062114   7497.357302  10326.438395  22676.668227   
6.936545e+09  17704.284667   7201.496123   9814.660948  22164.890781   

                9990047761    9990041105  ...    9990012399         60698  \
1.219232e+09  23889.526601  28637.853219  ...  15704.909985  18275.625929   
1.219232e+09  23843.170836  27766.668573  ...  15658.554221  18229.270165   
1.219232e+09  24098.510782  27521.362011  ...  15913.894166  18484.610110   
1.219232e+09  23092.396764  27840.723381  ...  14907.780148  17478.496092   
1.219232e+09  26769.408742  30192.259971  ...  18584.792126  21155.508070   
...                    ...           ...  ...           ...           ...   
6.936545e+09  35538.742043  19947.560309  ...  31395.483480  31717.438705   
6.936545e+09  35584.379819  19993.198085  ...  31441.121256  31763.076481   
5.699797e+09  24625.395536   3140.585137  ...  20482.136973  20804.092198   
6.936545e+09  35593.991166  20002.809432  ...  31450.732603  31772.687828   
6.936545e+09  35082.213719  19491.031985  ...  30938.955156  31260.910381   

                    104006       9999046         70907         20004  \
1.219232e+09  28450.724349  42746.021832  34629.025570  51262.035257   
1.219232e+09  27579.539704  41874.837187  34582.669805  50390.850612   
1.219232e+09  27334.233141  41629.530624  34838.009751  50145.544049   
1.219232e+09  27653.594512  41948.891995  33831.895733  50464.905420   
1.219232e+09  30005.131101  44300.428584  37508.907711  52816.442010   
...                    ...           ...           ...           ...   
6.936545e+09  18583.014972  32232.642028  46278.241012  19751.241179   
6.936545e+09  18628.652748  32278.279804  46323.878788  19796.878955   
5.699797e+09   7980.446281  22269.122637  35364.894505  28518.499700   
6.936545e+09  18638.264095  32287.891151  46333.490135  19806.490302   
6.936545e+09  18126.486648  31776.113704  45821.712688  19294.712855   

                9990014970    9990015483    9990012414    9990033919  
1.219232e+09  34991.657318  20804.008633  14601.491846  24130.277659  
1.219232e+09  34120.472673  20757.652869  14555.136081  24083.921894  
1.219232e+09  33875.166110  21012.992814  14810.476027  24339.261839  
1.219232e+09  34194.527480  20006.878796  13804.362009  23333.147822  
1.219232e+09  36546.064070  23683.890774  17481.373987  27010.159800  
...                    ...           ...           ...           ...  

In [134]:
list(OD_matrix2.min(axis=1))

[8021.665379385158,
 7150.480734345448,
 6905.174171567907,
 7224.535542220973,
 9576.072131801171,
 5259.304365341078,
 7110.690719008021,
 6129.46392221735,
 7683.38739979985,
 8648.997511301903,
 7206.387173073747,
 10371.883605030333,
 7344.833258543807,
 6334.4374029029905,
 4626.41005560665,
 6326.22309947231,
 7269.395126408801,
 6060.3129973190435,
 7748.404077896633,
 5760.279278074451,
 4267.289354750739,
 2272.5271880575756,
 6887.240470185855,
 3439.121080029571,
 4104.747727034381,
 4371.821671396186,
 2660.0995229039654,
 2047.0059569446246,
 1149.1397423816923,
 2002.8781289484439,
 1646.9317019806895,
 2445.0461244363955,
 1557.047779990241,
 2416.584258249283,
 2439.257530062435,
 2402.2117023628502,
 708.9536787546261,
 1642.7902918453026,
 1546.7570122004051,
 3600.0298473938697,
 2058.817972879772,
 4512.895628719849,
 1778.3172241178622,
 1277.7509448159844,
 2063.020771077071,
 2152.6110374131913,
 10111.30720807655,
 2922.164298115431,
 6240.6513733358815,
 684.0

In [135]:
OD_df_rehab = OD_matrix2

In [136]:
closest_facility_id_per_origin_rehab = OD_matrix2.idxmin(axis=1)

In [137]:
closest_facility_id_per_origin_rehab

1.219232e+09         78291
1.219232e+09         78291
1.219232e+09         78291
1.219232e+09         78291
1.219232e+09         78291
                   ...    
6.936545e+09         82567
6.936545e+09         82567
5.699797e+09    9990003939
6.936545e+09         82567
6.936545e+09         82567
Length: 79334, dtype: object

In [138]:
# origins that are within buffer
closest_facility_id_per_origin_rehab2 = closest_facility_id_per_origin_rehab[closest_facility_id_per_origin_rehab.index.isin(list(points_within['osm_id_left']))]
closest_facility_id_per_origin_rehab2

6.936545e+09    9990016667
6.936545e+09    9990016667
1.217922e+09        131376
1.226311e+09    9990005571
1.226311e+09    9990005571
                   ...    
1.217921e+09         42804
1.217921e+09        131376
1.217921e+09        131376
6.936545e+09    9990035067
7.294961e+09           497
Length: 10090, dtype: object

In [139]:
list(closest_facility_id_per_origin_rehab2)

[9990016667,
 9990016667,
 '131376',
 9990005571,
 9990005571,
 9990005571,
 9990005571,
 9990005571,
 9990005571,
 9990005571,
 9990005571,
 9990005571,
 9990005571,
 9990005571,
 9990005571,
 9990005571,
 9990005571,
 '93639',
 9990005571,
 '131376',
 9990005571,
 9990005571,
 9990034807,
 9990034807,
 9990034807,
 9990039456,
 9990039456,
 9990039456,
 '79106',
 9990039456,
 '57319',
 9990039456,
 9990039456,
 9990039456,
 9990016898,
 9990016898,
 9990034807,
 '26865',
 '26865',
 '26865',
 '26865',
 '26865',
 '26865',
 9990005571,
 9990005571,
 9990005571,
 9990005571,
 '93639',
 9990035183,
 '131376',
 '131376',
 9990035067,
 9990005571,
 '93639',
 '131376',
 9990044242,
 9990044242,
 '131376',
 '142521',
 '131376',
 9990035067,
 '93639',
 '93639',
 9990015104,
 '160984',
 '125693',
 9990044242,
 '160984',
 '131376',
 '131376',
 '93639',
 9990044242,
 9990044242,
 9990043945,
 9990044242,
 9990034807,
 9990034807,
 9990034807,
 9990034807,
 9990035067,
 9990035067,
 9990034807,
 9

In [140]:
closest_facility_id_per_origin_rehab2

6.936545e+09    9990016667
6.936545e+09    9990016667
1.217922e+09        131376
1.226311e+09    9990005571
1.226311e+09    9990005571
                   ...    
1.217921e+09         42804
1.217921e+09        131376
1.217921e+09        131376
6.936545e+09    9990035067
7.294961e+09           497
Length: 10090, dtype: object

In [141]:
OD_df_reg = OD_matrix

In [142]:
from collections import defaultdict

In [143]:
def group(lst, n):
  for i in range(0, len(lst), 1):
    val = lst[i:i+n]
    if len(val) == n:
      yield tuple(val)

In [144]:
#https://stackoverflow.com/questions/26367812/appending-to-list-in-python-dictionary
rehab_road_tracker = defaultdict(list)

In [145]:
rehab_origin_destination_pairs = []

In [146]:
def look_up(shortest_path, shortest_path_time, row, col):
    shortest_path_rehab_road_tracker = []
    edge_segements = list(group(shortest_path,2))
    for edge in edge_segements:
        try:    
            if G_adv_w_time_rehab[edge[0]][edge[1]][0]['Type'] == 'rehab':
                #print('rehab match')
                road_name = G_adv_w_time_rehab[edge[0]][edge[1]][0]['name']
                shortest_path_rehab_road_tracker.append(road_name)
                #break
        except:
            print(G_adv_w_time_rehab[edge[0]][edge[1]][0])
            print(edge[0])
            print(edge[1])
            global mismatch_count
            mismatch_count += 1
    
    if len(shortest_path_rehab_road_tracker) > 0:
        
        shortest_path_rehab_road_tracker = list(set(shortest_path_rehab_road_tracker))
        
        if len(shortest_path_rehab_road_tracker) > 1:
            print('This shortest path traversed more than one rehab roads')
        
        print(f"shortest_path_rehab_road_tracker is: {shortest_path_rehab_road_tracker}")

        for rehab_road in shortest_path_rehab_road_tracker:
            print(f"will append road name: {rehab_road} with shortest path time: {shortest_path_time}")
            rehab_road_tracker[rehab_road].append(shortest_path_time)

        rehab_origin_destination_pairs.append((row, col))

In [147]:
%time
mismatch_count = 0
for row, col in closest_facility_id_per_origin_rehab2.items():
    print(row)
    print(col)
    shortest_path = nx.dijkstra_path(G_adv_w_time_rehab, row, col, weight='time')
    shortest_path_time = OD_df_rehab.loc[row, col]
    look_up(shortest_path, shortest_path_time, row, col)

CPU times: user 2 µs, sys: 0 ns, total: 2 µs
Wall time: 4.05 µs
6936545281.0
9990016667
6936545287.0
9990016667
1217921704.0
131376
shortest_path_rehab_road_tracker is: ['mnar_anes']
will append road name: mnar_anes with shortest path time: 3600.0298473938697
1226310835.0
9990005571
1226311149.0
9990005571
1226311153.0
9990005571
1226311174.0
9990005571
1226311197.0
9990005571
1226311207.0
9990005571
1226311578.0
9990005571
1226311587.0
9990005571
shortest_path_rehab_road_tracker is: ['sbarah_sanahi']
will append road name: sbarah_sanahi with shortest path time: 1783.3586555657791
1226311625.0
9990005571
shortest_path_rehab_road_tracker is: ['sbarah_sanahi']
will append road name: sbarah_sanahi with shortest path time: 2668.5185365445964
1226311629.0
9990005571
shortest_path_rehab_road_tracker is: ['sbarah_sanahi']
will append road name: sbarah_sanahi with shortest path time: 1698.401067896967
1226311648.0
9990005571
1226311656.0
9990005571
shortest_path_rehab_road_tracker is: ['sbarah

shortest_path_rehab_road_tracker is: ['al_zone_jarmah_track']
will append road name: al_zone_jarmah_track with shortest path time: 2472.6904361834313
7294950039.0
131376
7294950043.0
119747
shortest_path_rehab_road_tracker is: ['taiz_to_al_turbah']
will append road name: taiz_to_al_turbah with shortest path time: 2075.322482337836
7294950048.0
131376
shortest_path_rehab_road_tracker is: ['mnar_anes']
will append road name: mnar_anes with shortest path time: 1701.8166007974992
7294950063.0
9990039456
shortest_path_rehab_road_tracker is: ['bajil_assaleef']
will append road name: bajil_assaleef with shortest path time: 1884.556656572886
7294950082.0
9990039456
shortest_path_rehab_road_tracker is: ['bajil_assaleef']
will append road name: bajil_assaleef with shortest path time: 1946.1583170663507
7294950084.0
131376
shortest_path_rehab_road_tracker is: ['mnar_anes']
will append road name: mnar_anes with shortest path time: 2223.217726909831
7294950085.0
5254
7294950090.0
9990005571
shortes

7294950978.0
9990005793
7294950979.0
142521
7294951002.0
9990024055
shortest_path_rehab_road_tracker is: ['al_zone_jarmah_track']
will append road name: al_zone_jarmah_track with shortest path time: 2966.3600839611845
7294951004.0
131376
shortest_path_rehab_road_tracker is: ['mnar_anes']
will append road name: mnar_anes with shortest path time: 1657.1172853268745
7294951005.0
9990044242
7294951015.0
9990045345
7294951016.0
9990045345
7294951019.0
9990045345
7294951069.0
9990045345
7294951071.0
9990048144
7294951078.0
9990004883
shortest_path_rehab_road_tracker is: ['alaman_suqe_alamasha']
will append road name: alaman_suqe_alamasha with shortest path time: 1341.0652867809729
7294951079.0
9990004883
shortest_path_rehab_road_tracker is: ['alaman_suqe_alamasha']
will append road name: alaman_suqe_alamasha with shortest path time: 1153.256231524659
7294951141.0
9990034807
shortest_path_rehab_road_tracker is: ['shriki_hamadi']
will append road name: shriki_hamadi with shortest path time: 28

9990005793
7294951855.0
9990005793
7294951856.0
9990005793
7294951857.0
9990005793
7294951858.0
9990005793
7294951859.0
9990005793
7294951860.0
9990005793
7294951861.0
9990005793
7294951862.0
9990005793
7294951863.0
9990005793
7294951864.0
9990005793
7294951866.0
9990005793
7294951867.0
9990005793
7294951868.0
9990005793
7294951869.0
9990005793
7294951870.0
9990005793
7294951871.0
9990005793
7294951874.0
9990005793
7294951875.0
9990005793
7294951876.0
9990005793
7294951877.0
9990005793
7294951893.0
9990005793
7294951894.0
9990005793
7294951895.0
9990005793
7294951896.0
9990005793
7294951897.0
9990005793
7294951898.0
9990005793
7294951899.0
9990005793
7294951900.0
9990005793
7294951927.0
9990005793
7294951928.0
9990005793
7294951929.0
9990005793
7294951930.0
9990005793
7294951931.0
9990005793
7294964641.0
9990005571
7294964640.0
9990005571
shortest_path_rehab_road_tracker is: ['sbarah_sanahi']
will append road name: sbarah_sanahi with shortest path time: 4216.634655181894
7294964656.0
9

shortest_path_rehab_road_tracker is: ['al_abr_to_seiyun']
will append road name: al_abr_to_seiyun with shortest path time: 9905.275029308912
7294956451.0
9990007290
7294956452.0
9990007290
7294956453.0
9990004883
shortest_path_rehab_road_tracker is: ['alaman_suqe_alamasha']
will append road name: alaman_suqe_alamasha with shortest path time: 2676.224918477175
7294956454.0
9990004883
shortest_path_rehab_road_tracker is: ['alaman_suqe_alamasha']
will append road name: alaman_suqe_alamasha with shortest path time: 2826.074572369264
7294956461.0
9990020104
7294956462.0
9990020104
7294956463.0
9990035067
shortest_path_rehab_road_tracker is: ['afiosh']
will append road name: afiosh with shortest path time: 803.2137534685165
7294956464.0
9990035067
shortest_path_rehab_road_tracker is: ['afiosh']
will append road name: afiosh with shortest path time: 1490.9533850536304
7294956465.0
9990035067
shortest_path_rehab_road_tracker is: ['afiosh']
will append road name: afiosh with shortest path time:

...

6936554097.0
20369
6936554099.0
9990015592
6936554101.0
26865
shortest_path_rehab_road_tracker is: ['taiz_to_al_turbah']
will append road name: taiz_to_al_turbah with shortest path time: 2127.2293447966194
1217882789.0
160984
shortest_path_rehab_road_tracker is: ['mansuriah_dir_maalm']
will append road name: mansuriah_dir_maalm with shortest path time: 1600.2974782888673
1217882790.0
160984
1217882839.0
160984
6936554226.0
121177
shortest_path_rehab_road_tracker is: ['modhfar_alll']
will append road name: modhfar_alll with shortest path time: 2442.247310241775
1217882873.0
160984
1217882877.0
160984
shortest_path_rehab_road_tracker is: ['mansuriah_dir_maalm']
will append road name: mansuriah_dir_maalm with shortest path time: 1232.2771830598917
1217882909.0
160984
shortest_path_rehab_road_tracker is: ['mansuriah_dir_maalm']
will append road name: mansuriah_dir_maalm with shortest path time: 1295.5274263467347
6936554324.0
5254
shortest_path_rehab_road_tracker is: ['2turbah_tor_albaha']

6936557001.0
9990016667
shortest_path_rehab_road_tracker is: ['hajdah_rasian']
will append road name: hajdah_rasian with shortest path time: 3459.1004344932535
6936557007.0
77811
6936557009.0
9990039456
shortest_path_rehab_road_tracker is: ['bajil_assaleef']
will append road name: bajil_assaleef with shortest path time: 4470.107579528431
6936557033.0
9990039456
shortest_path_rehab_road_tracker is: ['bajil_assaleef']
will append road name: bajil_assaleef with shortest path time: 2856.944779885641
6936557050.0
20369
6936557049.0
9990015592
1227060768.0
9990001018
1226274337.0
58064
6936557089.0
9990002665
1226274344.0
58064
1226274345.0
58064
1226274361.0
58064
1227060797.0
9990001018
1227060804.0
9990001018
6936557122.0
9990015104
1227060815.0
9990001018
6936557143.0
9990016667
6936557149.0
9990035067
shortest_path_rehab_road_tracker is: ['afiosh']
will append road name: afiosh with shortest path time: 1432.1393263481243
6936557150.0
9990035067
shortest_path_rehab_road_tracker is: ['afi

9990044242
7294958450.0
9990035067
shortest_path_rehab_road_tracker is: ['afiosh']
will append road name: afiosh with shortest path time: 4755.617856338322
7294958453.0
9990035067
shortest_path_rehab_road_tracker is: ['afiosh']
will append road name: afiosh with shortest path time: 4292.925856101493
6936540866.0
77811
shortest_path_rehab_road_tracker is: ['jbl_murad']
will append road name: jbl_murad with shortest path time: 2095.1624499560307
7294958487.0
9990035067
shortest_path_rehab_road_tracker is: ['afiosh']
will append road name: afiosh with shortest path time: 3711.5186053566617
7294958508.0
9990035067
shortest_path_rehab_road_tracker is: ['afiosh']
will append road name: afiosh with shortest path time: 4609.568690326032
7294958510.0
9990035067
shortest_path_rehab_road_tracker is: ['afiosh']
will append road name: afiosh with shortest path time: 4820.675870669328
7294958539.0
9990035067
shortest_path_rehab_road_tracker is: ['afiosh']
will append road name: afiosh with shortest 

shortest_path_rehab_road_tracker is: ['mnar_anes']
will append road name: mnar_anes with shortest path time: 2717.2866568894683
7294933966.0
131376
shortest_path_rehab_road_tracker is: ['mnar_anes']
will append road name: mnar_anes with shortest path time: 2687.5364395508896
7294933969.0
9990035067
This shortest path traversed more than one rehab roads
shortest_path_rehab_road_tracker is: ['ourod', 'afiosh']
will append road name: ourod with shortest path time: 2133.773209607505
will append road name: afiosh with shortest path time: 2133.773209607505
7294933971.0
9990044242
7294933972.0
9990044242
7294933973.0
93639
7294933974.0
9990044242
7294933976.0
131376
shortest_path_rehab_road_tracker is: ['mnar_anes']
will append road name: mnar_anes with shortest path time: 3135.9153625996687
7294933980.0
131376
shortest_path_rehab_road_tracker is: ['mnar_anes']
will append road name: mnar_anes with shortest path time: 1684.3086434379316
7294933981.0
131376
7294934189.0
9990004883
shortest_pat

1217920582.0
131376
shortest_path_rehab_road_tracker is: ['mnar_anes']
will append road name: mnar_anes with shortest path time: 3921.409602591975
1217920644.0
131376
shortest_path_rehab_road_tracker is: ['mnar_anes']
will append road name: mnar_anes with shortest path time: 3254.3767607387113
6936545101.0
9990035067
shortest_path_rehab_road_tracker is: ['afiosh']
will append road name: afiosh with shortest path time: 1515.574174430541
7294960930.0
497


In [148]:
mismatch_count

0

In [149]:
rehab_road_tracker

defaultdict(list,
            {'mnar_anes': [3600.0298473938697,
              1709.4742892962054,
              3094.5393064609248,
              3407.512149848607,
              1496.7251219684072,
              1361.8989682779195,
              1657.8322066072774,
              2014.737865085629,
              1818.2920955660338,
              1701.8166007974992,
              2223.217726909831,
              2640.3336650538854,
              2248.007763301578,
              3190.609350264574,
              1255.8816267138195,
              1483.6272713061408,
              1815.888691117479,
              3590.504399748028,
              3434.958463007588,
              1238.506224220627,
              3596.9710553721325,
              2161.9870257151238,
              1420.8925642284803,
              1613.3421221572485,
              1707.580234584872,
              1657.1172853268745,
              2193.9592669059098,
              2517.326687144064,
              1476.715745908

In [150]:
rehab_road_tracker_mean = {}

In [151]:
from statistics import mean

In [152]:
rehab_road_tracker_export = {}
for key, value in rehab_road_tracker.items():
    print(key)
    print(mean(value))
    print(len(value))
    rehab_road_tracker_export[key]=[mean(value),len(value)]

mnar_anes
2341.991464272139
270
sbarah_sanahi
2487.9878181043664
98
shriki_hamadi
2435.543274519907
253
bajil_assaleef
3186.3865722842725
46
Al Shurge- Al Hammadi & Sum Branches
3441.1634590409403
204
taiz_to_al_turbah
2038.5145756792008
1137
afiosh
2277.007271001731
1269
ribat_hiwah_mnwz
2625.7459464215476
121
akmat_hubaish
408.15327968371867
54
mansuriah_dir_maalm
1974.6190510708302
109
alaman_suqe_alamasha
1460.6213895783148
295
al_zone_jarmah_track
3013.395392714897
63
al_muaras_al_bajela
1416.9577606220284
9
jabal_arrabowah
972.8118794427222
21
jbl_murad
2739.5173944068442
97
morais
1457.0585846883648
1
al_abr_to_seiyun
11183.932778699305
4
talook
472.2831481761411
83
hajdah_rasian
3601.578724639808
165
jahaf_and_azarek
2546.3678830235117
32
modhfar_alll
2391.3384305805794
21
misrakh
1126.7783831388892
70
serhan
2475.535296733775
24
kir_all
1910.6413727712236
11
ourod
2751.908099312211
369
2turbah_tor_albaha
1836.7294849757325
240
kaniah_al_abdiah
2877.254963168671
79
ba_tays_rous

In [153]:
rehab_road_tracker_export

{'mnar_anes': [2341.991464272139, 270],
 'sbarah_sanahi': [2487.9878181043664, 98],
 'shriki_hamadi': [2435.543274519907, 253],
 'bajil_assaleef': [3186.3865722842725, 46],
 'Al Shurge- Al Hammadi & Sum Branches': [3441.1634590409403, 204],
 'taiz_to_al_turbah': [2038.5145756792008, 1137],
 'afiosh': [2277.007271001731, 1269],
 'ribat_hiwah_mnwz': [2625.7459464215476, 121],
 'akmat_hubaish': [408.15327968371867, 54],
 'mansuriah_dir_maalm': [1974.6190510708302, 109],
 'alaman_suqe_alamasha': [1460.6213895783148, 295],
 'al_zone_jarmah_track': [3013.395392714897, 63],
 'al_muaras_al_bajela': [1416.9577606220284, 9],
 'jabal_arrabowah': [972.8118794427222, 21],
 'jbl_murad': [2739.5173944068442, 97],
 'morais': [1457.0585846883648, 1],
 'al_abr_to_seiyun': [11183.932778699305, 4],
 'talook': [472.2831481761411, 83],
 'hajdah_rasian': [3601.578724639808, 165],
 'jahaf_and_azarek': [2546.3678830235117, 32],
 'modhfar_alll': [2391.3384305805794, 21],
 'misrakh': [1126.7783831388892, 70],
 '

In [154]:
rehab_road_tracker_export_df = pd.DataFrame.from_dict(rehab_road_tracker_export, orient='index',
                       columns=['mean_travel_time', 'num_of_trips'])

In [155]:
rehab_road_tracker_export_df.to_csv(r'output2/rehab_road_tracker_district_38N.csv')

In [156]:
rehab_origin_destination_pairs

[(1217921704.0, '131376'),
 (1226311587.0, 9990005571),
 (1226311625.0, 9990005571),
 (1226311629.0, 9990005571),
 (1226311656.0, 9990005571),
 (1226311663.0, 9990005571),
 (1226311682.0, 9990005571),
 (1226312289.0, 9990005571),
 (1226312302.0, 9990005571),
 (1226312343.0, 9990005571),
 (7294946282.0, 9990034807),
 (7294946283.0, 9990034807),
 (7294946284.0, 9990034807),
 (1224741436.0, 9990039456),
 (1224741469.0, 9990039456),
 (1224741480.0, 9990039456),
 (6936546113.0, 9990016898),
 (6936546165.0, 9990034807),
 (7294948623.0, '26865'),
 (7294948625.0, '26865'),
 (7294948626.0, '26865'),
 (7294948627.0, '26865'),
 (7294948628.0, '26865'),
 (7294948629.0, '26865'),
 (7294963921.0, 9990005571),
 (7294963929.0, 9990005571),
 (7294963995.0, 9990005571),
 (7294964000.0, 9990005571),
 (7294949586.0, '131376'),
 (7294949596.0, '131376'),
 (7294949599.0, 9990035067),
 (7294949609.0, '131376'),
 (7294949616.0, '131376'),
 (7294949625.0, '131376'),
 (7294949627.0, 9990035067),
 (7294949638.0,

#### Recorded all of the origin and destination IDs of the paths that pass through the rehab roads in rehab_road_tracker, now run again using these same ids but using the regular graph for a comparison

In [157]:
reg_road_tracker = defaultdict(list)

In [158]:
def look_up2(shortest_path, shortest_path_time):
    shortest_path_road_tracker = []
    edge_segements = list(group(shortest_path,2))
    for edge in edge_segements:
        try:           
            if G_adv_w_time[edge[0]][edge[1]][0]['Type'] == 'rehab':
                print('rehab match')
                road_name = G_adv_w_time[edge[0]][edge[1]][0]['name']
                shortest_path_road_tracker.append(road_name)
                #reg_road_tracker[road_name].append(shortest_path_time)
                #break
        except:
            print(G_adv_w_time[edge[0]][edge[1]][0])
            print(edge[0])
            print(edge[1])
            global mismatch_count2
            mismatch_count2 += 1
            
    if len(shortest_path_road_tracker) > 0:
        
        shortest_path_road_tracker = list(set(shortest_path_road_tracker))
        
        if len(shortest_path_road_tracker) > 1:
            print('This shortest path traversed more than one reg roads')
        
        print(f"shortest_path_road_tracker is: {shortest_path_road_tracker}")

        for reg_road in shortest_path_road_tracker:
            print(f"will append road name: {reg_road} with shortest path time: {shortest_path_time}")
            reg_road_tracker[reg_road].append(shortest_path_time)

In [159]:
%time
mismatch_count2 = 0
for origin, destination in rehab_origin_destination_pairs:
    shortest_path = nx.dijkstra_path(G_adv_w_time, origin, destination, weight='time')
    shortest_path_time = OD_df_reg.loc[origin, destination]
    look_up2(shortest_path, shortest_path_time)

CPU times: user 1e+03 ns, sys: 0 ns, total: 1e+03 ns
Wall time: 3.58 µs
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
shortest_path_road_tracker is: ['mnar_anes']
will append road name: mnar_anes with shortest path time: 6190.215177785103
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
shortest_path_road_tracker is: ['sbarah_sanahi']
will append road name: sbarah_sanahi with shortest path time: 2015.4365435542231
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
shortest_path_road_tracker is: ['sbarah_sanahi']
will append road name: sbarah_sanahi with shortest path time: 3044.5428802890883
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab m

rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
shortest_path_road_tracker is: ['afiosh']
will append road name: afiosh with shortest path time: 2601.3424745982843
rehab match
rehab match
shortest_path_road_tracker is: ['mnar_anes']
will append road name: mnar_anes with shortest path time: 1651.5986332630791
rehab match
rehab match
rehab 

rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
shortest_path_road_tracker is: ['afiosh']
will append road name: afiosh with shortest path time: 3698.714719302346
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
shortest_path_road_tracker is: ['afiosh']
will append road name: afiosh with shortest path time: 2916.005552425186
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
re

rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
shortest_path_road_tracker is: ['taiz_to_al_turbah']
will append road name: taiz_to_al_turbah with shortest path time: 1162.995318494865
rehab match
rehab match

rehab match
shortest_path_road_tracker is: ['taiz_to_al_turbah']
will append road name: taiz_to_al_turbah with shortest path time: 3437.1149415558807
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
shortest_path_road_tracker is: ['mnar_anes']
will append road name: mnar_anes with shortest path time: 3567.743292311544
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
shortest_path_road_tracker is: ['mnar_anes']
will append road name: mnar_anes with shortest path time: 3175.4173905592365
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
shortest_path_road_tracker is: ['mnar_anes']
will append road name: mnar_anes with shortest path time: 2215.9363091550704
rehab

...

rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
shortest_path_road_tracker is: ['Al Saheed Mountain- Bani Falah- Bani Zaid Alhada']
will append road name: Al Saheed Mountain- Bani Falah- Bani Zaid Alhada with shortest path time: 7588.105317836358
rehab match
rehab match
rehab match
rehab match
rehab match
shortest_path_road_tracker is: ['jabal_arrabowah']
will append road name: jabal_arrabowah with shortest path time: 1481.7840303728517
rehab match
rehab match
shortest_path_road_tracker is: ['afiosh']
will append road name: afiosh with shortest path time: 403.8870329600556
rehab match
rehab match
shortest_path_road_tracker is: ['afiosh']
will append road name: afiosh with shortest path time: 266.5527915867501
rehab match
rehab match
shortest_path_road_tracker is: ['afiosh']
will append road name: afiosh with shortest path time: 532.1917533807851
rehab match
rehab match
shortest_p

rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
shortest_path_road_tracker is: ['afiosh']
will append road name: afiosh with shortest path time: 6160.265426470802
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab mat

rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
shortest_path_road_tracker is: ['afiosh']
will append road name: afiosh with shortest path time: 4936.628810397741
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab mat

rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
shortest_path_road_tracker is: ['afiosh']
will append road name: afiosh with shortest path time: 2947.5156723335435
rehab match
rehab match
rehab match
shortest_path_road_tracker is: ['bajil_assaleef']
will append road name: bajil_assaleef with shortest path time: 5075.939349347844
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
shortest_path_road_tr

rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
shortest_path_road_tracker is: ['afiosh']
will append road name: afiosh with shortest path time: 4995.900292152156
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab match
rehab mat

In [160]:
reg_road_tracker_export = {}
for key, value in reg_road_tracker.items():
    print(key)
    print(mean(value))
    print(len(value))
    reg_road_tracker_export[key]=[mean(value),len(value)]

mnar_anes
3253.9668892716363
243
sbarah_sanahi
3085.7045897432918
98
shriki_hamadi
3514.768409914444
253
bajil_assaleef
4092.8123707396694
45
Al Shurge- Al Hammadi & Sum Branches
3865.6070977743507
127
taiz_to_al_turbah
2589.334264143183
1133
afiosh
3715.1785602008686
1269
ribat_hiwah_mnwz
3295.860274458499
121
akmat_hubaish
707.3898911463065
54
alaman_suqe_alamasha
2284.8942377404564
295
al_muaras_al_bajela
2235.76421323756
9
jabal_arrabowah
1384.2674434644014
21
jbl_murad
4173.28921182178
87
al_zone_jarmah_track
2770.63227566192
22
morais
1519.5893635331136
1
al_abr_to_seiyun
14320.6340613178
4
talook
812.140623011104
83
hajdah_rasian
4395.808956971342
146
mansuriah_dir_maalm
3173.2328464997804
74
jahaf_and_azarek
2755.792580305769
32
modhfar_alll
2843.3930328173883
21
misrakh
1794.6919669941883
70
serhan
3024.198724109173
24
kir_all
2788.0678663079707
11
ourod
3779.191309157895
369
2turbah_tor_albaha
3512.266823022475
237
kaniah_al_abdiah
4958.753370649445
79
ba_tays_rousod
6213.691

In [161]:
reg_road_tracker_export_df = pd.DataFrame.from_dict(reg_road_tracker_export, orient='index',
                       columns=['mean_travel_time', 'num_of_trips'])

In [162]:
reg_road_tracker_export_df.to_csv(r'output2/reg_road_tracker_district_38N.csv')